### Import Data

In [1]:
import pandas as pd
import seaborn as sns
import numpy as np

from sklearn import svm
from sklearn.metrics import f1_score
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import GridSearchCV
from sklearn.decomposition import PCA

import random
import os
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
import seaborn as sns

from sklearn.preprocessing import Normalizer
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import torch.utils.data as data_utils
from sklearn.preprocessing import StandardScaler, MinMaxScaler

import sklearn
import sklearn.preprocessing as sp
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import warnings
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from sklearn.manifold import TSNE

### Seed 

In [2]:
def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = True

seed_everything(41)

### One Class SVM without Scaling

In [54]:
train_df = pd.read_csv('train.csv').drop(columns=['ID'])
val_df = pd.read_csv('val.csv').drop(columns=['ID'])
val = val_df.iloc[:,:-1]
lab = val_df.iloc[:,-1]

In [55]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=10000, nu=0.001, verbose=True)
model.fit(train_df)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=10000, nu=0.001, verbose=True)

In [57]:
def get_pred_label(model, x, k):
  prob = model.score_samples(x)
  prob = torch.tensor(prob, dtype = torch.float)
  topk_indices = torch.topk(prob, k = k, largest = False).indices

  pred = torch.zeros(len(x), dtype = torch.long)
  pred[topk_indices] = 1
  return pred.tolist(), prob.tolist()

val_pred, val_prob = get_pred_label(model, val, 28)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.6893386388084752]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     28432
           1       0.39      0.37      0.38        30

    accuracy                           1.00     28462
   macro avg       0.70      0.68      0.69     28462
weighted avg       1.00      1.00      1.00     28462

tp :  11 , fp :  17 , tn :  28415 , fn :  19


#### Submission

In [ ]:
def get_pred_label_(model_pred):
    model_pred = np.where(model_pred == 1, 0, model_pred)
    model_pred = np.where(model_pred == -1, 1, model_pred)
    return model_pred

In [ ]:
test_df = pd.read_csv('test.csv').drop(columns=['ID'])

test_pred = model.predict(test_df)
test_pred = get_pred_label_(test_pred)

In [ ]:
submit = pd.read_csv('sample_submission.csv')

In [ ]:
submit['Class'] = test_pred
submit.to_csv('submit1.csv', index=False)

### Score

*   Public: 0.6458464983

*   Private: 0.6378488537


### One Class SVM with StandardScaler

In [ ]:
train_df = pd.read_csv('train.csv').drop(columns=['ID'])
val_df = pd.read_csv('val.csv').drop(columns=['ID'])
val = val_df.iloc[:,:-1]
lab = val_df.iloc[:,-1]

In [ ]:
std = StandardScaler()
train_df.iloc[:,:] = std.fit_transform(train_df)
val.iloc[:,:] = std.fit_transform(val)

In [ ]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=100000, nu=0.001, verbose=True)
model.fit(train_df)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=100000, nu=0.001, verbose=True)

In [ ]:
val_pred, val_prob = get_pred_label(model, val, 29)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.63521513188387]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     28432
           1       0.28      0.27      0.27        30

    accuracy                           1.00     28462
   macro avg       0.64      0.63      0.64     28462
weighted avg       1.00      1.00      1.00     28462

tp :  8 , fp :  21 , tn :  28411 , fn :  22


#### Submission

In [ ]:
def get_pred_label_(model_pred):
    model_pred = np.where(model_pred == 1, 0, model_pred)
    model_pred = np.where(model_pred == -1, 1, model_pred)
    return model_pred

test_df = pd.read_csv('test.csv').drop(columns=['ID'])

test_pred = model.predict(test_df)
test_pred = get_pred_label_(test_pred)

submit['Class'] = test_pred
submit.to_csv('submit2.csv', index=False)

### Score

*   Public: 0.615311725

*   Private: 0.6067083042


### One Class SVM with MinMaxScaler

In [ ]:
train_df = pd.read_csv('train.csv').drop(columns=['ID'])
val_df = pd.read_csv('val.csv').drop(columns=['ID'])
val = val_df.iloc[:,:-1]
lab = val_df.iloc[:,-1]

In [ ]:
col = train_df.columns

scaler_ = MinMaxScaler()
train_df_std = scaler_.fit_transform(train_df)
train_df_std_ = pd.DataFrame(data=train_df_std, columns=col)

model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=10000, nu=0.001, verbose=True)
model.fit(train_df_std_)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=10000, nu=0.001, verbose=True)

In [ ]:
col_ = val.columns

val = scaler_.transform(val)
val = pd.DataFrame(data=val, columns=col_)

In [ ]:
val_pred, val_prob = get_pred_label(model, val, 29)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.6691486079876962]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     28432
           1       0.34      0.33      0.34        30

    accuracy                           1.00     28462
   macro avg       0.67      0.67      0.67     28462
weighted avg       1.00      1.00      1.00     28462

tp :  10 , fp :  19 , tn :  28413 , fn :  20


In [ ]:
def get_pred_label_(model_pred):
    model_pred = np.where(model_pred == 1, 0, model_pred)
    model_pred = np.where(model_pred == -1, 1, model_pred)
    return model_pred

test_df = pd.read_csv('test.csv').drop(columns=['ID'])

col_t = test_df.columns
test_df_std = scaler_.transform(test_df)
test_df_std_ = pd.DataFrame(data=test_df_std, columns=col_t)

test_pred = model.predict(test_df_std_)
test_pred = get_pred_label_(test_pred)

submit['Class'] = test_pred
submit.to_csv('submit6.csv', index=False)

### Score

*   Public: 0.6370155638

*   Private: 0.6263939218

## 차원축소된 데이터셋(tSNE)을 이용한 One Class SVM

### One Class SVM with tSNE dataset (2 dimensional)

In [59]:
train_df = pd.read_csv('tsne_train.csv').drop(columns=['Unnamed: 0'])
val_df = pd.read_csv('tsne_valid.csv').drop(columns=['Unnamed: 0'])

In [60]:
val = pd.read_csv('val.csv').drop(columns=['ID'])
lab = val.iloc[:,-1]

In [61]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=10000, nu=0.001, verbose=True)
model.fit(train_df)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=10000, nu=0.001, verbose=True)

In [66]:
val_pred, val_prob = get_pred_label(model, val_df, 280)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.4972621613028579]
              precision    recall  f1-score   support

           0       1.00      0.99      0.99     28432
           1       0.00      0.00      0.00        30

    accuracy                           0.99     28462
   macro avg       0.50      0.50      0.50     28462
weighted avg       1.00      0.99      0.99     28462

tp :  0 , fp :  280 , tn :  28152 , fn :  30


### One Class SVM with normalized tSNE dataset (2 dimensional)

In [ ]:
train_df = pd.read_csv('tsne_train_standardscaled.csv').drop(columns=['Unnamed: 0'])
val_df = pd.read_csv('tsne_valid_standardscaled.csv').drop(columns=['Unnamed: 0'])

In [ ]:
val = pd.read_csv('val.csv').drop(columns=['ID'])
lab = val.iloc[:,-1]

In [ ]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=100000, nu=0.001, verbose=True)
model.fit(train_df)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=100000, nu=0.001, verbose=True)

In [ ]:
val_pred, val_prob = get_pred_label(model, val_df, 280)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.4972621613028579]
              precision    recall  f1-score   support

           0       1.00      0.99      0.99     28432
           1       0.00      0.00      0.00        30

    accuracy                           0.99     28462
   macro avg       0.50      0.50      0.50     28462
weighted avg       1.00      0.99      0.99     28462

tp :  0 , fp :  280 , tn :  28152 , fn :  30


In [ ]:
from sklearn.manifold import TSNE

scr = StandardScaler()
train_df = scr.fit_transform(train_df)

# 3차원 t-SNE Embedding
# n_components = 축소될 차원수를 설정
tsne_np = TSNE(n_components=3).fit_transform(train_df)

#numpy array -> DataFrame으로 변환
tsne_df = pd.DataFrame(tsne_np, columns = ['new_V1','new_V2','new_V3'])

/usr/local/lib/python3.8/dist-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


## 차원축소된 데이터셋(PCA)을 이용한 One Class SVM

### 주성분 3개로 진행 (Best Score!)

In [29]:
train_df = pd.read_csv('train.csv').drop(columns=['ID'])
valid_df = pd.read_csv('val.csv').drop(columns=['ID'])

In [30]:
std_scaler = StandardScaler()
train_std = std_scaler.fit_transform(train_df)

pca = PCA(n_components=3)
prcomponent = pca.fit_transform(train_std)

In [31]:
principal = pd.DataFrame(data=prcomponent, columns = ['pca_v1', 'pca_v2', 'pca_v3'])

In [32]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=100000, nu=0.001, verbose=True)
model.fit(principal)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=100000, nu=0.001, verbose=True)

In [33]:
valid_std = std_scaler.fit_transform(valid_df)
prcomponent_ = pca.fit_transform(valid_std)
principal_ = pd.DataFrame(data=prcomponent_, columns = ['pca_v1', 'pca_v2', 'pca_v3'])

In [92]:
val_pred, val_prob = get_pred_label(model, principal_, 28)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.9309641419574388]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     28432
           1       0.89      0.83      0.86        30

    accuracy                           1.00     28462
   macro avg       0.95      0.92      0.93     28462
weighted avg       1.00      1.00      1.00     28462

tp :  25 , fp :  3 , tn :  28429 , fn :  5


In [37]:
def get_pred_label_(model_pred):
    model_pred = np.where(model_pred == 1, 0, model_pred)
    model_pred = np.where(model_pred == -1, 1, model_pred)
    return model_pred

submit = pd.read_csv('sample_submission.csv')

test_df = pd.read_csv('test.csv').drop(columns=['ID'])

In [41]:
col_t = test_df.columns
test_df_std = std_scaler.fit_transform(test_df)
test_df_std_ = pd.DataFrame(data=test_df_std, columns=col_t)

prcomponent_ = pca.fit_transform(test_df_std_)
principal_ = pd.DataFrame(data=prcomponent_, columns = ['pca_v1', 'pca_v2', 'pca_v3'])

test_pred = model.predict(principal_)
test_pred = get_pred_label_(test_pred)

submit['Class'] = test_pred
submit.to_csv('submit.csv', index=False)

### 주성분 5개로 진행

In [67]:
train_df = pd.read_csv('train.csv').drop(columns=['ID'])
valid_df = pd.read_csv('val.csv').drop(columns=['ID'])

In [68]:
std_scaler = StandardScaler()
train_std = std_scaler.fit_transform(train_df)

pca = PCA(n_components=5)
prcomponent = pca.fit_transform(train_std)

In [69]:
principal = pd.DataFrame(data=prcomponent, columns = ['pca_v1', 'pca_v2', 'pca_v3', 'pca_v4', 'pca_v5'])

In [70]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=100000, nu=0.001, verbose=True)
model.fit(principal)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=100000, nu=0.001, verbose=True)

In [71]:
valid_std = std_scaler.fit_transform(valid_df)
prcomponent_ = pca.fit_transform(valid_std)
principal_ = pd.DataFrame(data=prcomponent_, columns = ['pca_v1', 'pca_v2', 'pca_v3', 'pca_v4', 'pca_v5'])

In [79]:
val_pred, val_prob = get_pred_label(model, principal_, 28)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.7756334613616767]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     28432
           1       0.57      0.53      0.55        30

    accuracy                           1.00     28462
   macro avg       0.79      0.77      0.78     28462
weighted avg       1.00      1.00      1.00     28462

tp :  16 , fp :  12 , tn :  28420 , fn :  14


### 상관계수가 큰 컬럼 5개를 추출한 One Class SVM

In [7]:
train_df = pd.read_csv('train.csv').drop(columns=['ID'])
valid_df = pd.read_csv('val.csv').drop(columns=['ID'])
lab = valid_df.iloc[:, -1]

In [11]:
valid_df = valid_df.sample(frac=1)

fraud_df = valid_df.loc[valid_df['Class'] == 1]
non_fraud_df = valid_df.loc[valid_df['Class'] == 0][:len(fraud_df)]

normal_distributed_df = pd.concat([fraud_df, non_fraud_df])

new_val_df = normal_distributed_df.sample(frac=1, random_state=42)

sub_sample_corr = new_val_df.corr()

for idx, (k,v) in enumerate(sub_sample_corr['Class'][:-1].sort_values().items()):
    print(idx, k, v)

0 V14 -0.7919156805432372
1 V12 -0.694052914208697
2 V9 -0.6481055655764667
3 V10 -0.6287404670598054
4 V3 -0.6251728295023341
5 V16 -0.5778927156265873
6 V17 -0.5606362058642058
7 V7 -0.5315297270949396
8 V6 -0.52777899662657
9 V1 -0.4891989976430318
10 V5 -0.47962412475070637
11 V18 -0.4595143442360974
12 V24 -0.3097156216538107
13 V27 -0.1903390407505014
14 V28 -0.1597817539186821
15 V15 -0.10564117510148473
16 V25 -0.07641320164273982
17 V30 0.017924141621928208
18 V21 0.027097898723037035
19 V29 0.03269931422082556
20 V13 0.040606742334083325
21 V26 0.13466891799174832
22 V23 0.15367343532098957
23 V8 0.2030439817879839
24 V20 0.23503325995522292
25 V19 0.24606639021308993
26 V22 0.26128731558913126
27 V2 0.607550733802673
28 V11 0.6968678068328256
29 V4 0.7656143893983943


In [12]:
train_df = train_df[['V4', 'V9', 'V11', 'V12', 'V14']]
valid_df = valid_df[['V4', 'V9', 'V11', 'V12', 'V14']]

In [13]:
std_scaler = StandardScaler()
train_std = std_scaler.fit_transform(train_df)

model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=100000, nu=0.001, verbose=True)
model.fit(train_std)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=100000, nu=0.001, verbose=True)

In [19]:
def get_pred_label(model, x, k):
  prob = model.score_samples(x)
  prob = torch.tensor(prob, dtype = torch.float)
  topk_indices = torch.topk(prob, k = k, largest = False).indices

  pred = torch.zeros(len(x), dtype = torch.long)
  pred[topk_indices] = 1
  return pred.tolist(), prob.tolist()

val_pred, val_prob = get_pred_label(model, valid_df, 130)
val_score = f1_score(lab, val_pred, average='macro')
print(f'Validation F1 Score : [{val_score}]')
print(classification_report(lab, val_pred))
tn, fp, fn, tp = confusion_matrix(lab, val_pred).ravel()
print('tp : ', tp, ', fp : ', fp, ', tn : ', tn, ', fn : ', fn)

Validation F1 Score : [0.4985906560496089]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     28432
           1       0.00      0.00      0.00        30

    accuracy                           0.99     28462
   macro avg       0.50      0.50      0.50     28462
weighted avg       1.00      0.99      1.00     28462

tp :  0 , fp :  130 , tn :  28302 , fn :  30


/usr/local/lib/python3.8/dist-packages/sklearn/base.py:443: UserWarning: X has feature names, but OneClassSVM was fitted without feature names
  warnings.warn(


## One Class SVM + LGBM

In [4]:
!pip install optuna

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 365.3/365.3 KB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 210.5/210.5 KB 20.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.7/78.7 KB 11.8 MB/s eta 0:00:00


In [5]:
from sklearn.model_selection import StratifiedKFold
from tqdm.notebook import tqdm

import lightgbm 
from lightgbm import LGBMClassifier
import optuna
from optuna.samplers import TPESampler

In [47]:
train = pd.read_csv('train.csv')
valid = pd.read_csv('val.csv')
test = pd.read_csv('test.csv')

In [21]:
trainset = train.drop(['ID'] , axis = 1) 
testset = test.drop(['ID'] , axis = 1)
fraud_ratio = valid['Class'].values.sum() / len(valid)

In [22]:
model = svm.OneClassSVM(gamma=0.0001, kernel='rbf', max_iter=100000, nu=0.001, verbose=True)
model.fit(trainset)

[LibSVM]

OneClassSVM(gamma=0.0001, max_iter=100000, nu=0.001, verbose=True)

In [23]:
def get_pred_label(model, x, k):
  prob = model.score_samples(x)
  prob = torch.tensor(prob, dtype = torch.float)
  topk_indices = torch.topk(prob, k = k, largest = False).indices

  pred = torch.zeros(len(x), dtype = torch.long)
  pred[topk_indices] = 1
  return pred , prob

In [24]:
test_pred, _ = get_pred_label(model, testset, 280)

In [25]:
onesvm_pred = np.array(test_pred)

In [26]:
train_pred, _ = get_pred_label(model, trainset, 118)
Y = np.array(train_pred)

In [27]:
score = []
def lgb_optimization(trial):
    score = []
    skf = StratifiedKFold(n_splits = 5 , random_state = 42 , shuffle = True)
    for train_fold, test_fold in tqdm(skf.split(trainset, Y), desc = 'k_fold'):
        X_train, X_test, y_train, y_test = trainset.iloc[train_fold], trainset.iloc[test_fold], Y[train_fold], Y[test_fold] 
        
        params = {            
            "boosting_type" : trial.suggest_categorical('boosting_type',['dart','gbdt']),
            "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
            "n_estimators": trial.suggest_int("n_estimators", 100, 300, step=10),
            "max_depth": trial.suggest_int("max_depth", 1, 15),
            "num_leaves": trial.suggest_int("num_leaves", 2, 256),
            "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 1),
            "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 1),
            "subsample": trial.suggest_float("subsample", 0.4, 1.0),
            "subsample_freq": trial.suggest_int("subsample_freq", 1, 30),
            "colsample_bytree": trial.suggest_float("colsample_bytree", 0.1, 1.0),
            "min_child_samples": trial.suggest_int("min_child_samples", 5, 50),
            "max_bin": trial.suggest_int("max_bin", 50, 100),
            "verbosity": -1,
            "random_state": trial.suggest_int("random_state", 1, 10000)
        }
        model_lgb = LGBMClassifier(**params)
        model_lgb.fit(X_train, y_train)
        lgb_cv_pred = model_lgb.predict(X_test)
        
        score_cv = f1_score(Y[test_fold] , lgb_cv_pred , average = 'macro')
        
        score.append(score_cv)
    print(score)
    return np.mean(score) 

In [28]:
sampler = TPESampler()
optim = optuna.create_study(
    study_name="lgb_parameter_opt",
    direction="maximize",
    sampler=sampler,
)
#optim.optimize(lgb_optimization, n_trials=1)
optim.optimize(lgb_optimization, n_trials=99999)
print("Best macro-F1:", optim.best_value)

[I 2023-02-17 08:04:42,025] A new study created in memory with name: lgb_parameter_opt


k_fold: 0it [00:00, ?it/s]

<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
<ipython-input-27-e6c104a30c0a>:10: F

[0.7329815148716595, 0.8459779678616244, 0.8554126701496512, 0.7350963241434765, 0.8212086945596181]


k_fold: 0it [00:00, ?it/s]

...

<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
<ipython-input-27-e6c104a30c0a>:10: F

[0.7042597025781622, 0.7689669517924365, 0.8088600434547093, 0.8093479621593219, 0.7497141852079852]


k_fold: 0it [00:00, ?it/s]

<ipython-input-27-e6c104a30c0a>:10: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  "learning_rate": trial.suggest_uniform('learning_rate', 0.2, 0.99),
[W 2023-02-17 09:10:15,205] Trial 263 failed with parameters: {'boosting_type': 'gbdt', 'learning_rate': 0.2605978788595659, 'n_estimators': 300, 'max_depth': 9, 'num_leaves': 21, 'reg_alpha': 0.5380967357731221, 'reg_lambda': 0.40950109752841174, 'subsample': 0.5583453494905541, 'subsample_freq': 10, 'colsample_bytree': 0.2723064601081618, 'min_child_samples': 29, 'max_bin': 98, 'random_state': 5599} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/usr/local/lib/python3.8/dist-packages/optuna/study/_optimize.py", line 200, in _run_trial
    value_or_values = func(trial)
  File "<ipython-input-27-e6c104a30c0a>", line 25, in

KeyboardInterrupt: ignored

In [27]:
params = {'boosting_type': 'gbdt', 'learning_rate': 0.27931562561080087,
 'n_estimators': 180, 'max_depth': 2, 'num_leaves': 79, 'reg_alpha': 0.7804924821497133,
 'reg_lambda': 0.6483886637315736, 'subsample': 0.5046737928606037, 'subsample_freq': 27,
 'colsample_bytree': 0.2884662481524903, 'min_child_samples': 39, 'max_bin': 69}
#random_state = 3294

In [28]:
model2 = LGBMClassifier(**params , random_state = 3294)
model2.fit(trainset, Y)
lgb_pred = model2.predict(testset)

In [31]:
valid.drop(columns=['ID'], inplace=True)

In [35]:
lgb_cv_pred = model2.predict(valid.iloc[:, :-1])
        
score_cv = f1_score(valid.iloc[:, -1] , lgb_cv_pred , average = 'macro')

In [34]:
score_cv

0.6872362683733032

In [29]:
sub = pd.read_csv('sample_submission.csv')
sub['Class'] = onesvm_pred|lgb_pred # Ensemble 
sub.to_csv('final_submission.csv' , index = False)

### tSNE 3차원 시도

In [48]:
scr = StandardScaler()
train_df = scr.fit_transform(train)

# 3차원 t-SNE Embedding
# n_components = 축소될 차원수를 설정
tsne_np = TSNE(n_components=3).fit_transform(train_df)

#numpy array -> DataFrame으로 변환
tsne_df = pd.DataFrame(tsne_np, columns = ['new_V1','new_V2','new_V3'])

/usr/local/lib/python3.8/dist-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


KeyboardInterrupt: ignored